In [1]:
import csv
import numpy as np
import bokeh.io
import bokeh.plotting
import pandas as pd
from bokeh.models import Legend
from bokeh.layouts import gridplot

bokeh.io.output_notebook()
colors = bokeh.palettes.colorblind['Colorblind'][6]

Loading BokehJS ...

In [3]:
df = pd.read_csv('../data/echem/PCAelectrolysis_05_22_18.csv')
time = df['time']

# Subtract inoculation time
time = time - 170.6 * 1000
# Convert to hours
time = time / 3600

Pnitro_sp_charge = np.array(-df['p1_C'])
Pnitro_po_charge = np.array(-df['p2_C'])
PhzOxC_charge = np.array(-df['p3_C'])
PhzOxA_charge = np.array(-df['p0_C'])

time = np.array(time)
start = np.where(time < 0)[0][-1]
baseline_mono = np.mean([Pnitro_sp_charge[start], Pnitro_po_charge[start], PhzOxC_charge[start], PhzOxA_charge[start]])

def ox(coulombs):
    electrons_per_coulomb = 6.424 * 10 ** 18
    electrons_per_pca = 2
    avogadros_number = 6.022 * 10 ** 23 # molecules per mole
    volume = 0.1 # liters
    
    # multiply by 10 ** 6 for µM units
    return coulombs * electrons_per_coulomb / (electrons_per_pca * avogadros_number * volume) * 10 ** 6
#     return coulombs * 6.424 * 10 ** 18 / (2 * 6.022 * 10 ** 23) * 10 ** 6 * 10

def turnover(ox, concentration):
    # both in units of micromolar
    
    return ox /concentration

mono_pre_inoc = ox(baseline_mono)
Pnitro_sp_ox = ox(Pnitro_sp_charge[-100]) - mono_pre_inoc
Pnitro_po_ox = ox(Pnitro_po_charge[-100]) - mono_pre_inoc
PhzOxC_ox = ox(PhzOxC_charge[-100]) - mono_pre_inoc
PhzOxA_ox = ox(PhzOxA_charge[-100]) - mono_pre_inoc

In [4]:
print(Pnitro_sp_ox, Pnitro_po_ox, PhzOxA_ox, PhzOxC_ox)

439.90318830953174 219.61823314513455 1602.6663899036866 1650.6703752906008


In [5]:
print(turnover(Pnitro_sp_ox, 100), turnover(Pnitro_po_ox, 100), turnover(PhzOxA_ox, 100), turnover(PhzOxC_ox, 100))

4.399031883095318 2.1961823314513453 16.026663899036866 16.506703752906006


In [6]:
def plot_charge(df, title=None):
    
    p = bokeh.plotting.figure(height = 300,
                              width = 800,
#                               background_fill_color = 'floralwhite',
                              x_axis_label = 'Time (hrs)',
                              y_axis_label = 'Charge (Coulombs)',
                              title = title
                                )
    
    time = df['time']
    time = time - 170.6 * 1000
    time = time / 3600
    Pnitro_sp_charge = -df['p1_C']
    Pnitro_po_charge = -df['p2_C']
    PhzOxC_charge = -df['p3_C']
    PhzOxA_charge = -df['p0_C']
    
    r0 = p.line(time, Pnitro_sp_charge, line_width = 2, color = colors[0])
    r1 = p.line(time, Pnitro_po_charge, line_width = 2, color = colors[1])
    r2 = p.line(time, PhzOxA_charge, line_width = 2, color = colors[2])
    r3 = p.line(time, PhzOxC_charge, line_width = 2, color = colors[3])
#     r4 = p.line(170.6*1000, np.linspace(0, -36, 100), line_width = 2, line_dash = 'dashed', color = 'black')
    
    legend = Legend(items=[
    ("PhzOx A" , [r2]),
    ('PhzOx C', [r3]),    
    ("P. nitroreducens spreader"   , [r0]),
    ("P. nitroreducens pointer" , [r1]),

#     ('Inoculation time', [r4])    
        ], location=(0, 143))

    p.add_layout(legend, 'right')
    p.legend.label_text_font_style = 'italic'
    p.legend.border_line_alpha = 0
    
    return p

In [7]:
p = plot_charge(df)
bokeh.io.show(p)

In [8]:
def plot_current(df, title = None):
    p = bokeh.plotting.figure(height = 300,
                              width = 800,
#                               background_fill_color = 'floralwhite',
                              x_axis_label = 'Time (hrs)',
                              y_axis_label = 'Current (μA)',
#                               y_axis_type = 'log',
                              title = title
                                )
    
    time = df['time']
    t2 = np.array(time)
    start = np.where(t2 > 170.6 * 1000)[0][0]
    time = time - 170.6 * 1000
    time = time/3600
    Pnitro_sp_current = df['p1_I'] * 10 ** 6
    Pnitro_po_current = df['p2_I'] * 10 ** 6
    PhzOxC_current = df['p3_I'] * 10 ** 6
    PhzOxA_current = df['p0_I'] * 10 ** 6
    
    r1 = p.line(time[start:], Pnitro_po_current[start:], line_width = 2, color = colors[1], alpha = 0.8)
    r0 = p.line(time[start:], Pnitro_sp_current[start:], line_width = 2, color = colors[0], alpha = 0.8)
    r2 = p.line(time[start:], PhzOxA_current[start:], line_width = 2, color = colors[2], alpha = 0.8)
    r3 = p.line(time[start:], PhzOxC_current[start:], line_width = 2, color = colors[3], alpha = 0.8)
#     r4 = p.line(170.6*1000, np.linspace(0, -36, 100), line_width = 2, line_dash = 'dashed', color = 'black')
    
    legend = Legend(items=[
    ("PhzOx A" , [r2]),
    ('PhzOx C', [r3]),    
    ("P. nitroreducens spreader"   , [r0]),
    ("P. nitroreducens pointer" , [r1]),

#     ('Inoculation time', [r4])    
        ], location=(0, 143))

    p.add_layout(legend, 'right')
    p.legend.label_text_font_style = 'italic'
    p.legend.border_line_alpha = 0
    
    return p

In [9]:
p2 = plot_current(df)
bokeh.io.show(p2)

In [10]:
df_mixed = pd.read_csv('../data/echem/PCAox_04_25_18_electrolysisData.csv')
time_mixed = df_mixed['time']
time_mixed = time_mixed - 111.1 * 1000
time_mixed = time_mixed / 3600
PA_charge = np.array(-df_mixed['C2_C'])
PhzOxA_charge = np.array(-df_mixed['C4_C'])
PhzOxC_charge = np.array(-df_mixed['C6_C'])

time_mixed = np.array(time_mixed)
start = np.where(time_mixed < 0)[0][-1]
baseline_mixed = np.mean([PA_charge[start], PhzOxA_charge[start], PhzOxC_charge[start]])

mixed_pre_inoc = ox(baseline_mixed)
PA_ox = ox(PA_charge[-1]) - mixed_pre_inoc
PhzOxC_ox = ox(PhzOxC_charge[-1]) - mixed_pre_inoc
PhzOxA_ox = ox(PhzOxA_charge[-1]) - mixed_pre_inoc
print(PA_ox, PhzOxA_ox, PhzOxC_ox)

578.3591276430864 5938.804162515223 2237.1635115686922


In [11]:
print(turnover(PA_ox, 100), turnover(PhzOxA_ox, 100), turnover(PhzOxC_ox, 100))

5.7835912764308635 59.388041625152226 22.37163511568692


In [12]:
def plot_mixed_current(df, title = None):
    p = bokeh.plotting.figure(height = 300,
                          width = 800,
                          x_axis_label = 'Time (hrs)',
                          y_axis_label = 'Current (μA)',
#                               y_axis_type = 'log',
                          title = title)
    time = df['time']
    t2 = np.array(time)
    start = np.where(t2 > 111.1 * 1000)[0][0]
    time = time - 111.1 * 1000
    time = time/3600
    PA_current = df['C2_I'] * 10 ** 6
    PhzOxA_current = df['C4_I'] * 10 ** 6
    PhzOxC_current = df['C6_I'] * 10 ** 6
    
    r1 = p.line(time[start:-100], PA_current[start:-100], line_width = 2, color = colors[1], alpha = 0.8)
    r2 = p.line(time[start:-100], PhzOxA_current[start:-100], line_width = 2, color = colors[2], alpha = 0.8)
    r3 = p.line(time[start:-100], PhzOxC_current[start:-100], line_width = 2, color = colors[3], alpha = 0.8)
#     r4 = p.line(170.6*1000, np.linspace(0, -36, 100), line_width = 2, line_dash = 'dashed', color = 'black')
    
    legend = Legend(items=[
    
    ("PhzOxA" , [r2]),
    ('PhzOxC', [r3]),
    ("Pseudomonas aeruginosa" , [r1]),
#     ('Inoculation time', [r4])    
        ], location=(0, 166))

    p.add_layout(legend, 'right')
    p.legend.label_text_font_style = 'italic'
    p.legend.border_line_alpha = 0
    
    return p    

In [13]:
p5 = plot_mixed_current(df_mixed)
bokeh.io.show(p5)

In [15]:
df_LB = pd.read_csv('../data/cfus/2018_06_02_mBraunElectrode_LB_CFUcounts.csv')
df_Min = pd.read_csv('../data/cfus/2018_06_02_mBraunElectrode_MinMed_CFUcounts.csv')

In [16]:
def plot_cfus(df, title = None):
    p = bokeh.plotting.figure(height = 200,
                          width = 850,
#                           background_fill_color = 'floralwhite',
                          x_axis_label = 'Time (hrs)',
                          y_axis_label = 'CFUs',
                          y_axis_type = 'log',
                          title = title
                            )
    
    c1 = df[(df.Plate == 'Chamber 1')]
    c2 = df[(df.Plate == 'Chamber 2')]
    c3 = df[(df.Plate == 'Chamber 3')]
    c4 = df[(df.Plate == 'Chamber 4')]
    c5 = df[(df.Plate == 'Chamber 5')]
    c6 = df[(df.Plate == 'Chamber 6')]
    
    time = c1['Time (ks)']
    time = time - 170.6
    time = time * 1000 / 3600

    c1_density = c1['cfuPerMl']
    c2_density = c2['cfuPerMl']
    c3_density = c3['cfuPerMl']
    c4_density = c4['cfuPerMl']
    c5_density = c5['cfuPerMl']
    c6_density = c6['cfuPerMl']
    
    r0 = p.line(time, c1_density, line_width = 2, color = colors[0])
    r1 = p.square(time, c1_density, line_width = 1, color = colors[0])
    
    r2 = p.line(time, c2_density, line_width = 2, color = colors[1])
    r3 = p.square(time, c2_density, line_width = 1, color = colors[1])
    
    r4 = p.line(time, c3_density, line_width = 2, color = colors[3])
    r5 = p.square(time, c3_density, line_width = 1, color = colors[3])
    
    r6 = p.line(time, c4_density, line_width = 2, color = colors[2])
    r7 = p.square(time, c4_density, line_width = 1, color = colors[2])
    
    r8 = p.line(time, c5_density, line_width = 2, color = colors[4])
    r9 = p.square(time, c5_density, line_width = 1, color = colors[4])
    
    r10 = p.line(time, c6_density, line_width = 2, color = colors[5])
    r11 = p.square(time, c6_density, line_width = 1, color = colors[5])
    
    legend = Legend(items=[
    ("P. nitroreducens spreader (PCA + electrode)"   , [r0, r1]),
    ("P. nitroreducens pointer (PCA + electrode)" , [r2, r3]),
    ("PhzOxC (PCA + electrode)" , [r4, r5]),
    ('PhzOxA (PCA + electrode)', [r6, r7]),
    ('P. nitroreducens pointer (alone)', [r8, r9]),
    ('P. nitroreducens spreader (alone)', [r10, r11])
        ], location=(0, -3))

    p.add_layout(legend, 'right')
    p.legend.label_text_font_style = 'italic'
    
    return p
    

In [17]:
p3 = plot_cfus(df_LB)
bokeh.io.show(p3)

In [18]:
%load_ext watermark
%watermark -v -p numpy,bokeh,pandas,jupyterlab

Python implementation: CPython
Python version       : 3.9.15
IPython version      : 8.7.0

numpy     : 1.23.4
bokeh     : 2.3.3
pandas    : 1.5.2
jupyterlab: 3.5.0

